<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Christoph Berke </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Computer-Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060"> Vorlesung &mdash; Programmiertechniken 4 </h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Sommersemester 2023</h3>
<!--<h3 style="font-weight:bold; text-align: center; margin: 0px; font-size: 15px; padding:0px; margin-bottom: 20px;">Website: <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml</a></h3> -->

<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml</a></font>

<font size="4" color="#606060">**Themen dieses Notebooks**: <span style="color:#606060">  </span> 
    "Messdaten" herunterladen, Visualisieren, Fehlerfortpflanzung, Parameterbestimmung durch Fitten, LaTeX-kompatible Ausgabe
<hr style="height:.3px"> 

## Beschreibung des (Gedanken-)Experiments

Im Folgenden wollen wir erarbeiten, wie man experimentelle Daten, die zum Beispiel während eines Praktikumsversuchs gewonnen wurden, mit Julia verarbeiten kann. Ein im Grundstudium häufig durchgeführtes Experiment ist das [Pohlsche Rad](https://de.wikipedia.org/wiki/Pohlsches_Rad) als Beispiel für resonante und chaotische Schwingvorgänge.

Daran angelehnt betrachten wir die folgende Differentialgleichung eines **getriebenen, gedämpften Oszillators**,

$\quad m\ddot{x} + \gamma\dot{x}+kx = F\sin(\omega t).$

### Wir machen zwei Versuche:

1. Wir schalten Dämpfung und Triebkraft aus ($\gamma = 0, F = 0$) und bestimmen die Masse $m$ und Schwingungsperiode $T$ des freien Oszillators.
2. Wir treiben den gedämpften Oszillator mit der konstanten Kraft $F$ bei variierenden Frequenzen $\omega$ und messen die Amplitude $A$ der Oszillation.

Aus den Ergebnissen zu 1 können wir die Federkonstante $k$ berechnen.

Aus den Ergebnissen zu 2 können wir die Dämpfung $\gamma$ bestimmen.

### "Messdaten" herunterladen:

**CSV Datei** ("Comma-separated values") mit Daten der Massen- und **Periodenmessung** (Versuch 1): https://tinyurl.com/y3bbrklk

**Excel Datei** mit Daten der **Resonanzmessung** (Versuch 2): https://tinyurl.com/y5t3qjkb

In [ ]:
download("http://www.thp.uni-koeln.de/trebst/Lectures/CompPhys-2023/period.csv", "period.csv")
download("http://www.thp.uni-koeln.de/trebst/Lectures/CompPhys-2023/resonance.xlsx", "resonance.xlsx");

Links: **[CSVFiles.jl](https://github.com/queryverse/CSVFiles.jl), [DataFrames.jl](https://github.com/JuliaData/DataFrames.jl)** ([Dokumentation](http://juliadata.github.io/DataFrames.jl/stable/))

Die Daten zu Versuch 2 (Resonanzmessung) liegen z.B. in einer Excel Datei `daten.xlsx` vor.

In [ ]:
using XLSX

Links: **[XLSX.jl](https://felipenoris.github.io/XLSX.jl/stable/)**

In [ ]:
xf = XLSX.readxlsx("resonance.xlsx")

In [ ]:
xf["Resonanzmessung!A1:C85"]

In [ ]:
resonance_data = Float64.(xf["Resonanzmessung!A3:C85"])

In [ ]:
ω = resonance_data[:,1]
A = resonance_data[:,2]
ΔA = resonance_data[:,3];

## Visualisieren

In [ ]:
using CairoMakie

In [ ]:
fig, ax, eb = errorbars(ω, A, ΔA)
scatterlines!(ax, ω, A, markersize = 2)

ax.title = "Schwingungsamplitude vs. Motorfrequenz"
ax.xlabel = "Motorfrequenz ω" 
ax.ylabel = "Schwingungsamplitude A"

fig

# 3. Federkonstante $k$ bestimmen (Automatische Fehlerfortpflanzung)

In [ ]:
using Measurements
import Measurements: value, uncertainty

Links: **[Measurements.jl](https://github.com/JuliaPhysics/Measurements.jl)** ([Dokumentation](https://juliaphysics.github.io/Measurements.jl/stable/))

Wir führen nun die Werte und Fehlerinformationen unserer Daten in `Measurements` zusammen.

Links: [Statistics](https://docs.julialang.org/en/v1/stdlib/Statistics/#Statistics) (Standard Library = Paket das mit Julia ausgeliefert wird (keine Installation notwendig))

Aus `mass_mean` und `T_mean` können wir nun die Federkonstante samt Fehler bestimmen.

$T = 2\pi\sqrt{\dfrac{m}{k}} \ \  \Rightarrow \ \ k = \left( \dfrac{2\pi}{T} \right)^2 m$

## 4. Bestimmen von $\gamma$ (Fitten)

Aus der exakten Lösung der Bewegungsgleichung wissen wir, dass die Amplitude die folgende Form besitzt:

$\quad A = \dfrac{F}{\sqrt{m^2 (\frac{k}{m} - \omega^2)^2 + \gamma^2 \omega^2}}$

Bis auf die Dämpfung $\gamma$ kennen wir alle Größen. Wir können diese Relation also an die Daten fitten und $\gamma$ extrahieren.

Links: [LsqFit.jl](https://github.com/JuliaNLSolvers/LsqFit.jl)

In [ ]:
F = 1.69 # konstante Kraft
m = value(mass_mean)
k = value(k_measurement)

# Fit definieren
# p = Parameter des Fits (Array)
function model(ω, p)
    γ = p[1]
    @. F / sqrt(m^2 * (k / m - ω^2)^2 + γ^2 * ω^2)
end

# 5. Darstellung der Ergebnisse im $\LaTeX$ - Look + Speichern als PDF Datei

In [ ]:
fig, ax, eb = errorbars(ω, A, ΔA, color =:deepskyblue3)
scatter!(ax, ω, A, markersize = 6, label = L"Messdaten$$", color =:deepskyblue3)
lines!(ω, model(ω, γ), label=L"Fit$$", color = :orange1)

ax.title = L"Schwingungsamplitude vs. Motorfrequenz$$"
ax.titlesize = 22
ax.xlabel = L"Motorfrequenz $\omega$" 
ax.ylabel = L"Schwingungsamplitude $A$"
ax.xlabelsize = 18
ax.ylabelsize = 18

ax.xticks = ([0.6,0.8,1,1.2,1.4], [L"0.6", L"0.8", L"1",L"1.2",L"1.4"] )
ax.yticks = ([0,5,10,15], [L"0", L"5", L"10", L"15"])

leg = Legend(fig[1,1], ax, tellwidth = false, margin = (0,20,0,20), valign = :top, halign = :right)

fig

In [ ]:
save("Schwingungsamplitude.pdf", fig)

# 6. Wo findet man externe Julia Pakete?

Eine Übersicht von Paketen gibt es z.B. unter https://juliaobserver.com/ und https://pkg.julialang.org/docs/.

Viele Pakete sind in sogenannten GitHub Organisationen, z.B. JuliaMath oder JuliaQuantum, zusammengefasst. Diese sind auf https://julialang.org/community/ unter *Julia GitHub Groups* gelistet.

Hilfe und Informationen zu Paketen findet man auf deren Webseiten (auf github). Diese findet man z.B. indem man nach "**Paketname jl**" sucht.

Beispiel DataFrames: https://github.com/JuliaData/DataFrames.jl

In [ ]:
@which curve_fit(model, ω, A, [0.5])

In [ ]:
@edit curve_fit(model, ω, A, [0.5])